Downloading and using the images in imagenet today (04/18/2020) is actually surprisingly difficult. The imagenet website requires you to request access, but I never got approval. They also have a list of image URLs but some of them are no longer valid. Another way to get the images is to use `academictorrents.com`. I have not been able to find an alternative source for these images. This notebook documents how I was able to download and format the data.

# Import

In [67]:
from pathlib import Path
import shutil
import os
import pandas as pd

# Config

In [7]:
dir_data = Path('/data')

# LSVRC 2012

I guess this is the set released in the year 2012. I used the following two links:

* training - [https://academictorrents.com/details/a306397ccf9c2ead27155983c254227c0fd938e2](https://academictorrents.com/details/a306397ccf9c2ead27155983c254227c0fd938e2)
* validation - [https://academictorrents.com/details/5d6d0df7ed81efd49ca99ea4737e0ae5e3a5f2e5](https://academictorrents.com/details/5d6d0df7ed81efd49ca99ea4737e0ae5e3a5f2e5)

Even though these are for "object detection" these contain just the images and the class labels based on the file names.

In [19]:
dir_imagenet_2012 = dir_data/'IMAGENET'/'2012'
dir_imagenet_2012.mkdir(parents=True, exist_ok=True)

### Download and format the training data

In [20]:
dir_trn = dir_imagenet_2012/'TRN'
dir_trn.mkdir(exist_ok=True)
file_trn_torrent = dir_trn/'trn.torrent'
file_trn_tar = dir_trn/'trn.tar'

Download the torrent file:

In [ ]:
!wget https://academictorrents.com/download/a306397ccf9c2ead27155983c254227c0fd938e2.torrent -O {file_trn_torrent}

Use `ctorrent` to download the tar file:

In [22]:
!ctorrent {file_trn_torrent} -s {file_trn_tar}

META INFO
Announce: https://academictorrents.com/announce.php
Alternates:
 1. udp://tracker.coppersurfer.tk:6969
 2. udp://tracker.opentrackr.org:1337/announce
 3. udp://tracker.openbittorrent.com:80/announce
Created On: Fri Oct 16 10:02:22 2015
Piece length: 2097152
Created with: Transmission/2.82 (14160)
FILES INFO
<1> /data/IMAGENET/2012/TRN/trn.tar [147897477120]
Total: 141046 MB
Creating file "/data/IMAGENET/2012/TRN/trn.tar"
Listening on 0.0.0.0:2705
Press 'h' or '?' for help (display/control client options).
- 7/1/10 [12201/70524/70524] 24406MB,0MB | 21911,0K/s | 11136,0K E:0,38 Quittin

Untar file:

In [24]:
!tar -xvf {file_trn_tar} -C {dir_trn}

n01440764.tar
n01443537.tar
n01484850.tar
n01491361.tar
n01494475.tar
n01496331.tar
n01498041.tar
n01514668.tar
n01514859.tar
n01518878.tar
n01530575.tar
n01531178.tar
n01532829.tar
n01534433.tar
n01537544.tar
n01558993.tar
n01560419.tar
n01580077.tar
n01582220.tar
n01592084.tar
n01601694.tar
n01608432.tar
n01614925.tar
n01616318.tar
n01622779.tar
n01629819.tar
n01630670.tar
n01631663.tar
n01632458.tar
n01632777.tar
n01641577.tar
n01644373.tar
n01644900.tar
n01664065.tar
n01665541.tar
n01667114.tar
n01667778.tar
n01669191.tar
n01675722.tar
n01677366.tar
n01682714.tar
n01685808.tar
n01687978.tar
n01688243.tar
n01689811.tar
n01692333.tar
n01693334.tar
n01694178.tar
n01695060.tar
n01697457.tar
n01698640.tar
n01704323.tar
n01728572.tar
n01728920.tar
n01729322.tar
n01729977.tar
n01734418.tar
n01735189.tar
n01737021.tar
n01739381.tar
n01740131.tar
n01742172.tar
n01744401.tar
n01748264.tar
n01749939.tar
n01751748.tar
n01753488.tar
n01755581.tar
n01756291.tar
n01768244.tar
n01770081.tar
n01770

n03478589.tar
n03481172.tar
n03482405.tar
n03483316.tar
n03485407.tar
n03485794.tar
n03492542.tar
n03494278.tar
n03495258.tar
n03496892.tar
n03498962.tar
n03527444.tar
n03529860.tar
n03530642.tar
n03532672.tar
n03534580.tar
n03535780.tar
n03538406.tar
n03544143.tar
n03584254.tar
n03584829.tar
n03590841.tar
n03594734.tar
n03594945.tar
n03595614.tar
n03598930.tar
n03599486.tar
n03602883.tar
n03617480.tar
n03623198.tar
n03627232.tar
n03630383.tar
n03633091.tar
n03637318.tar
n03642806.tar
n03649909.tar
n03657121.tar
n03658185.tar
n03661043.tar
n03662601.tar
n03666591.tar
n03670208.tar
n03673027.tar
n03676483.tar
n03680355.tar
n03690938.tar
n03691459.tar
n03692522.tar
n03697007.tar
n03706229.tar
n03709823.tar
n03710193.tar
n03710637.tar
n03710721.tar
n03717622.tar
n03720891.tar
n03721384.tar
n03724870.tar
n03729826.tar
n03733131.tar
n03733281.tar
n03733805.tar
n03742115.tar
n03743016.tar
n03759954.tar
n03761084.tar
n03763968.tar
n03764736.tar
n03769881.tar
n03770439.tar
n03770679.tar
n03773

Remove tar and torrent file:

In [25]:
file_trn_torrent.unlink()
file_trn_tar.unlink()

In [38]:
files_class_tar = list(dir_trn.glob('*.tar'))
len(files_class_tar)

1000

There are 1000 classes, so it seems each tar corresponds to each class

In [41]:
def _process_class_tar(file_class_tar):
    dir_class = dir_trn/file_class_tar.stem
    dir_class.mkdir(exist_ok=True)
    shutil.move(file_class_tar.as_posix(), dir_class)
    os.system(f'tar -xvf {dir_class/file_class_tar.name} -C {dir_class}')
    (dir_class/file_class_tar.name).unlink()

In [42]:
for file_class_tar in files_class_tar:
    _process_class_tar(file_class_tar)

NOTE: Do not convert class folders to the class name. For example, there are two "crane" classes, one of the animal and the other of the machine...

Copy class labels to train directory

In [48]:
shutil.copy('train.txt', dir_trn/'trn.txt')

PosixPath('/data/IMAGENET/2012/TRN/trn.txt')

### Download and format the validation data

In [49]:
dir_val = dir_imagenet_2012/'VAL'
dir_val.mkdir(exist_ok=True)
file_val_torrent = dir_val/'val.torrent'
file_val_tar = dir_val/'val.tar'

Download the torrent file:

In [50]:
!wget https://academictorrents.com/download/5d6d0df7ed81efd49ca99ea4737e0ae5e3a5f2e5.torrent -O {file_val_torrent}

--2020-04-18 13:09:52--  https://academictorrents.com/download/5d6d0df7ed81efd49ca99ea4737e0ae5e3a5f2e5.torrent
Resolving academictorrents.com (academictorrents.com)... 142.4.19.35
Connecting to academictorrents.com (academictorrents.com)|142.4.19.35|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: unspecified [application/x-bittorrent]
Saving to: ‘/data/IMAGENET/2012/VAL/val.torrent’

/data/IMAGENET/2012     [  <=>               ]  63.50K   194KB/s    in 0.3s    

2020-04-18 13:09:53 (194 KB/s) - ‘/data/IMAGENET/2012/VAL/val.torrent’ saved [65021]



Use `ctorrent` to download the tar file:

In [53]:
!ctorrent {file_val_torrent} -s {file_val_tar}

META INFO
Announce: https://academictorrents.com/announce.php
Alternates:
 1. udp://tracker.coppersurfer.tk:6969
 2. udp://tracker.opentrackr.org:1337/announce
 3. udp://tracker.openbittorrent.com:80/announce
Created On: Fri Oct 16 13:16:53 2015
Piece length: 2097152
Created with: Transmission/2.82 (14160)
FILES INFO
<1> /data/IMAGENET/2012/VAL/val.tar [6744924160]
Total: 6432 MB
Creating file "/data/IMAGENET/2012/VAL/val.tar"
Listening on 0.0.0.0:2705
Press 'h' or '?' for help (display/control client options).
- 10/4/16 [16/3217/3217] 42MB,0MB | 21617,0K/s | 24400,0K E:0,1 Quitting       

Untar file:

In [54]:
!tar -xvf {file_val_tar} -C {dir_val}

ILSVRC2012_val_00046108.JPEG
ILSVRC2012_val_00044030.JPEG
ILSVRC2012_val_00042898.JPEG
ILSVRC2012_val_00041481.JPEG
ILSVRC2012_val_00039493.JPEG
ILSVRC2012_val_00037864.JPEG
ILSVRC2012_val_00037578.JPEG
ILSVRC2012_val_00033095.JPEG
ILSVRC2012_val_00031091.JPEG
ILSVRC2012_val_00030154.JPEG
ILSVRC2012_val_00029819.JPEG
ILSVRC2012_val_00029360.JPEG
ILSVRC2012_val_00028777.JPEG
ILSVRC2012_val_00028553.JPEG
ILSVRC2012_val_00027575.JPEG
ILSVRC2012_val_00025401.JPEG
ILSVRC2012_val_00024855.JPEG
ILSVRC2012_val_00023386.JPEG
ILSVRC2012_val_00022933.JPEG
ILSVRC2012_val_00021388.JPEG
ILSVRC2012_val_00021057.JPEG
ILSVRC2012_val_00020878.JPEG
ILSVRC2012_val_00020583.JPEG
ILSVRC2012_val_00018525.JPEG
ILSVRC2012_val_00018454.JPEG
ILSVRC2012_val_00017993.JPEG
ILSVRC2012_val_00017876.JPEG
ILSVRC2012_val_00017779.JPEG
ILSVRC2012_val_00017000.JPEG
ILSVRC2012_val_00015032.JPEG
ILSVRC2012_val_00015001.JPEG
ILSVRC2012_val_00014754.JPEG
ILSVRC2012_val_00014387.JPEG
ILSVRC2012_val_00013565.JPEG
ILSVRC2012_val

ILSVRC2012_val_00007036.JPEG
ILSVRC2012_val_00006705.JPEG
ILSVRC2012_val_00006123.JPEG
ILSVRC2012_val_00004497.JPEG
ILSVRC2012_val_00003694.JPEG
ILSVRC2012_val_00003664.JPEG
ILSVRC2012_val_00000691.JPEG
ILSVRC2012_val_00047883.JPEG
ILSVRC2012_val_00047079.JPEG
ILSVRC2012_val_00047046.JPEG
ILSVRC2012_val_00045681.JPEG
ILSVRC2012_val_00044906.JPEG
ILSVRC2012_val_00044293.JPEG
ILSVRC2012_val_00044222.JPEG
ILSVRC2012_val_00043865.JPEG
ILSVRC2012_val_00042683.JPEG
ILSVRC2012_val_00042297.JPEG
ILSVRC2012_val_00042244.JPEG
ILSVRC2012_val_00041969.JPEG
ILSVRC2012_val_00041658.JPEG
ILSVRC2012_val_00041230.JPEG
ILSVRC2012_val_00038573.JPEG
ILSVRC2012_val_00038095.JPEG
ILSVRC2012_val_00037142.JPEG
ILSVRC2012_val_00036864.JPEG
ILSVRC2012_val_00035950.JPEG
ILSVRC2012_val_00034785.JPEG
ILSVRC2012_val_00034449.JPEG
ILSVRC2012_val_00034288.JPEG
ILSVRC2012_val_00033363.JPEG
ILSVRC2012_val_00033173.JPEG
ILSVRC2012_val_00031933.JPEG
ILSVRC2012_val_00031554.JPEG
ILSVRC2012_val_00031287.JPEG
ILSVRC2012_val

ILSVRC2012_val_00008433.JPEG
ILSVRC2012_val_00008335.JPEG
ILSVRC2012_val_00007726.JPEG
ILSVRC2012_val_00007547.JPEG
ILSVRC2012_val_00003691.JPEG
ILSVRC2012_val_00003327.JPEG
ILSVRC2012_val_00001925.JPEG
ILSVRC2012_val_00001568.JPEG
ILSVRC2012_val_00048123.JPEG
ILSVRC2012_val_00047276.JPEG
ILSVRC2012_val_00046629.JPEG
ILSVRC2012_val_00044642.JPEG
ILSVRC2012_val_00043776.JPEG
ILSVRC2012_val_00043201.JPEG
ILSVRC2012_val_00041705.JPEG
ILSVRC2012_val_00038257.JPEG
ILSVRC2012_val_00038247.JPEG
ILSVRC2012_val_00037960.JPEG
ILSVRC2012_val_00037230.JPEG
ILSVRC2012_val_00036890.JPEG
ILSVRC2012_val_00036433.JPEG
ILSVRC2012_val_00036267.JPEG
ILSVRC2012_val_00034040.JPEG
ILSVRC2012_val_00033476.JPEG
ILSVRC2012_val_00033222.JPEG
ILSVRC2012_val_00033200.JPEG
ILSVRC2012_val_00031965.JPEG
ILSVRC2012_val_00031068.JPEG
ILSVRC2012_val_00029262.JPEG
ILSVRC2012_val_00028706.JPEG
ILSVRC2012_val_00028459.JPEG
ILSVRC2012_val_00026017.JPEG
ILSVRC2012_val_00025437.JPEG
ILSVRC2012_val_00025098.JPEG
ILSVRC2012_val

ILSVRC2012_val_00045258.JPEG
ILSVRC2012_val_00045055.JPEG
ILSVRC2012_val_00044132.JPEG
ILSVRC2012_val_00043905.JPEG
ILSVRC2012_val_00042356.JPEG
ILSVRC2012_val_00041203.JPEG
ILSVRC2012_val_00039955.JPEG
ILSVRC2012_val_00039574.JPEG
ILSVRC2012_val_00039172.JPEG
ILSVRC2012_val_00037837.JPEG
ILSVRC2012_val_00037639.JPEG
ILSVRC2012_val_00037472.JPEG
ILSVRC2012_val_00032954.JPEG
ILSVRC2012_val_00032759.JPEG
ILSVRC2012_val_00032573.JPEG
ILSVRC2012_val_00032071.JPEG
ILSVRC2012_val_00031738.JPEG
ILSVRC2012_val_00030015.JPEG
ILSVRC2012_val_00028663.JPEG
ILSVRC2012_val_00028247.JPEG
ILSVRC2012_val_00025579.JPEG
ILSVRC2012_val_00024452.JPEG
ILSVRC2012_val_00024322.JPEG
ILSVRC2012_val_00023880.JPEG
ILSVRC2012_val_00021119.JPEG
ILSVRC2012_val_00019687.JPEG
ILSVRC2012_val_00018771.JPEG
ILSVRC2012_val_00018745.JPEG
ILSVRC2012_val_00018733.JPEG
ILSVRC2012_val_00017093.JPEG
ILSVRC2012_val_00016615.JPEG
ILSVRC2012_val_00014986.JPEG
ILSVRC2012_val_00014493.JPEG
ILSVRC2012_val_00013960.JPEG
ILSVRC2012_val

ILSVRC2012_val_00010647.JPEG
ILSVRC2012_val_00009040.JPEG
ILSVRC2012_val_00008728.JPEG
ILSVRC2012_val_00007301.JPEG
ILSVRC2012_val_00005700.JPEG
ILSVRC2012_val_00004516.JPEG
ILSVRC2012_val_00003975.JPEG
ILSVRC2012_val_00002880.JPEG
ILSVRC2012_val_00002384.JPEG
ILSVRC2012_val_00001229.JPEG
ILSVRC2012_val_00049077.JPEG
ILSVRC2012_val_00048666.JPEG
ILSVRC2012_val_00048553.JPEG
ILSVRC2012_val_00046732.JPEG
ILSVRC2012_val_00044522.JPEG
ILSVRC2012_val_00043081.JPEG
ILSVRC2012_val_00042758.JPEG
ILSVRC2012_val_00040455.JPEG
ILSVRC2012_val_00039784.JPEG
ILSVRC2012_val_00037552.JPEG
ILSVRC2012_val_00036074.JPEG
ILSVRC2012_val_00035605.JPEG
ILSVRC2012_val_00032470.JPEG
ILSVRC2012_val_00032335.JPEG
ILSVRC2012_val_00029736.JPEG
ILSVRC2012_val_00029168.JPEG
ILSVRC2012_val_00028586.JPEG
ILSVRC2012_val_00027676.JPEG
ILSVRC2012_val_00027667.JPEG
ILSVRC2012_val_00025126.JPEG
ILSVRC2012_val_00025075.JPEG
ILSVRC2012_val_00022418.JPEG
ILSVRC2012_val_00021933.JPEG
ILSVRC2012_val_00020933.JPEG
ILSVRC2012_val

...

ILSVRC2012_val_00005111.JPEG
ILSVRC2012_val_00003666.JPEG
ILSVRC2012_val_00002977.JPEG
ILSVRC2012_val_00002661.JPEG
ILSVRC2012_val_00002121.JPEG
ILSVRC2012_val_00002093.JPEG
ILSVRC2012_val_00001106.JPEG
ILSVRC2012_val_00000868.JPEG
ILSVRC2012_val_00000664.JPEG
ILSVRC2012_val_00049673.JPEG
ILSVRC2012_val_00049510.JPEG
ILSVRC2012_val_00048839.JPEG
ILSVRC2012_val_00048621.JPEG
ILSVRC2012_val_00043669.JPEG
ILSVRC2012_val_00043361.JPEG
ILSVRC2012_val_00042102.JPEG
ILSVRC2012_val_00038234.JPEG
ILSVRC2012_val_00037073.JPEG
ILSVRC2012_val_00036803.JPEG
ILSVRC2012_val_00036711.JPEG
ILSVRC2012_val_00035983.JPEG
ILSVRC2012_val_00033910.JPEG
ILSVRC2012_val_00033106.JPEG
ILSVRC2012_val_00030761.JPEG
ILSVRC2012_val_00030242.JPEG
ILSVRC2012_val_00028638.JPEG
ILSVRC2012_val_00027377.JPEG
ILSVRC2012_val_00027065.JPEG
ILSVRC2012_val_00025038.JPEG
ILSVRC2012_val_00024866.JPEG
ILSVRC2012_val_00024780.JPEG
ILSVRC2012_val_00024200.JPEG
ILSVRC2012_val_00024124.JPEG
ILSVRC2012_val_00022086.JPEG
ILSVRC2012_val

ILSVRC2012_val_00022635.JPEG
ILSVRC2012_val_00021647.JPEG
ILSVRC2012_val_00020894.JPEG
ILSVRC2012_val_00020732.JPEG
ILSVRC2012_val_00020353.JPEG
ILSVRC2012_val_00019970.JPEG
ILSVRC2012_val_00018893.JPEG
ILSVRC2012_val_00014454.JPEG
ILSVRC2012_val_00014274.JPEG
ILSVRC2012_val_00014242.JPEG
ILSVRC2012_val_00012550.JPEG
ILSVRC2012_val_00011107.JPEG
ILSVRC2012_val_00010190.JPEG
ILSVRC2012_val_00009927.JPEG
ILSVRC2012_val_00008630.JPEG
ILSVRC2012_val_00008080.JPEG
ILSVRC2012_val_00007911.JPEG
ILSVRC2012_val_00007310.JPEG
ILSVRC2012_val_00007275.JPEG
ILSVRC2012_val_00005371.JPEG
ILSVRC2012_val_00004636.JPEG
ILSVRC2012_val_00002696.JPEG
ILSVRC2012_val_00001204.JPEG
ILSVRC2012_val_00000901.JPEG
ILSVRC2012_val_00048919.JPEG
ILSVRC2012_val_00048335.JPEG
ILSVRC2012_val_00047060.JPEG
ILSVRC2012_val_00046764.JPEG
ILSVRC2012_val_00046651.JPEG
ILSVRC2012_val_00045940.JPEG
ILSVRC2012_val_00045501.JPEG
ILSVRC2012_val_00044793.JPEG
ILSVRC2012_val_00044204.JPEG
ILSVRC2012_val_00043196.JPEG
ILSVRC2012_val

ILSVRC2012_val_00016130.JPEG
ILSVRC2012_val_00015576.JPEG
ILSVRC2012_val_00014957.JPEG
ILSVRC2012_val_00013862.JPEG
ILSVRC2012_val_00013506.JPEG
ILSVRC2012_val_00012904.JPEG
ILSVRC2012_val_00012610.JPEG
ILSVRC2012_val_00012039.JPEG
ILSVRC2012_val_00011511.JPEG
ILSVRC2012_val_00010612.JPEG
ILSVRC2012_val_00009933.JPEG
ILSVRC2012_val_00006887.JPEG
ILSVRC2012_val_00006209.JPEG
ILSVRC2012_val_00005820.JPEG
ILSVRC2012_val_00004852.JPEG
ILSVRC2012_val_00003698.JPEG
ILSVRC2012_val_00003179.JPEG
ILSVRC2012_val_00001448.JPEG
ILSVRC2012_val_00000425.JPEG
ILSVRC2012_val_00000147.JPEG
ILSVRC2012_val_00048764.JPEG
ILSVRC2012_val_00047394.JPEG
ILSVRC2012_val_00047261.JPEG
ILSVRC2012_val_00046558.JPEG
ILSVRC2012_val_00046330.JPEG
ILSVRC2012_val_00046233.JPEG
ILSVRC2012_val_00045871.JPEG
ILSVRC2012_val_00045795.JPEG
ILSVRC2012_val_00045652.JPEG
ILSVRC2012_val_00045278.JPEG
ILSVRC2012_val_00044660.JPEG
ILSVRC2012_val_00044102.JPEG
ILSVRC2012_val_00043677.JPEG
ILSVRC2012_val_00041277.JPEG
ILSVRC2012_val

ILSVRC2012_val_00043541.JPEG
ILSVRC2012_val_00043531.JPEG
ILSVRC2012_val_00043437.JPEG
ILSVRC2012_val_00043365.JPEG
ILSVRC2012_val_00042759.JPEG
ILSVRC2012_val_00041538.JPEG
ILSVRC2012_val_00040452.JPEG
ILSVRC2012_val_00040218.JPEG
ILSVRC2012_val_00038648.JPEG
ILSVRC2012_val_00038132.JPEG
ILSVRC2012_val_00037546.JPEG
ILSVRC2012_val_00035418.JPEG
ILSVRC2012_val_00034786.JPEG
ILSVRC2012_val_00033403.JPEG
ILSVRC2012_val_00033347.JPEG
ILSVRC2012_val_00029401.JPEG
ILSVRC2012_val_00028827.JPEG
ILSVRC2012_val_00027789.JPEG
ILSVRC2012_val_00025005.JPEG
ILSVRC2012_val_00024397.JPEG
ILSVRC2012_val_00024176.JPEG
ILSVRC2012_val_00023819.JPEG
ILSVRC2012_val_00023449.JPEG
ILSVRC2012_val_00023041.JPEG
ILSVRC2012_val_00022780.JPEG
ILSVRC2012_val_00022000.JPEG
ILSVRC2012_val_00021612.JPEG
ILSVRC2012_val_00018969.JPEG
ILSVRC2012_val_00018196.JPEG
ILSVRC2012_val_00016344.JPEG
ILSVRC2012_val_00015770.JPEG
ILSVRC2012_val_00015113.JPEG
ILSVRC2012_val_00013328.JPEG
ILSVRC2012_val_00013062.JPEG
ILSVRC2012_val

ILSVRC2012_val_00038045.JPEG
ILSVRC2012_val_00036677.JPEG
ILSVRC2012_val_00035442.JPEG
ILSVRC2012_val_00034564.JPEG
ILSVRC2012_val_00033924.JPEG
ILSVRC2012_val_00033735.JPEG
ILSVRC2012_val_00032115.JPEG
ILSVRC2012_val_00029316.JPEG
ILSVRC2012_val_00027984.JPEG
ILSVRC2012_val_00027010.JPEG
ILSVRC2012_val_00026602.JPEG
ILSVRC2012_val_00026020.JPEG
ILSVRC2012_val_00024127.JPEG
ILSVRC2012_val_00022546.JPEG
ILSVRC2012_val_00021402.JPEG
ILSVRC2012_val_00018850.JPEG
ILSVRC2012_val_00017484.JPEG
ILSVRC2012_val_00017031.JPEG
ILSVRC2012_val_00015846.JPEG
ILSVRC2012_val_00015765.JPEG
ILSVRC2012_val_00015105.JPEG
ILSVRC2012_val_00012719.JPEG
ILSVRC2012_val_00012244.JPEG
ILSVRC2012_val_00009116.JPEG
ILSVRC2012_val_00007660.JPEG
ILSVRC2012_val_00007603.JPEG
ILSVRC2012_val_00006963.JPEG
ILSVRC2012_val_00006390.JPEG
ILSVRC2012_val_00006204.JPEG
ILSVRC2012_val_00005990.JPEG
ILSVRC2012_val_00005659.JPEG
ILSVRC2012_val_00004890.JPEG
ILSVRC2012_val_00004220.JPEG
ILSVRC2012_val_00003883.JPEG
ILSVRC2012_val

Remove tar and torrent file:

In [56]:
file_val_torrent.unlink()
file_val_tar.unlink()

Copy class labels to validation directory

In [57]:
shutil.copy('val.txt', dir_val/'val.txt')

PosixPath('/data/IMAGENET/2012/VAL/val.txt')

### Format the test data

After some googling, I was able to find a test set hosted here:

* test - [http://169.44.201.108:7002/imagenet/test/ILSVRC2012_img_test.tar](http://169.44.201.108:7002/imagenet/test/ILSVRC2012_img_test.tar)

It also houses the training and validation sets, but I'm not sure how long the above will stay online, so I'll leave the academic torrent instructions there

In [59]:
dir_tst = dir_imagenet_2012/'TST'
file_tst_tar = dir_tst/'ILSVRC2012_img_test.tar'

In [60]:
!tar -xvf {file_tst_tar} -C {dir_tst}

ILSVRC2012_test_00000001.JPEG
ILSVRC2012_test_00000002.JPEG
ILSVRC2012_test_00000003.JPEG
ILSVRC2012_test_00000004.JPEG
ILSVRC2012_test_00000005.JPEG
ILSVRC2012_test_00000006.JPEG
ILSVRC2012_test_00000007.JPEG
ILSVRC2012_test_00000008.JPEG
ILSVRC2012_test_00000009.JPEG
ILSVRC2012_test_00000010.JPEG
ILSVRC2012_test_00000011.JPEG
ILSVRC2012_test_00000012.JPEG
ILSVRC2012_test_00000013.JPEG
ILSVRC2012_test_00000014.JPEG
ILSVRC2012_test_00000015.JPEG
ILSVRC2012_test_00000016.JPEG
ILSVRC2012_test_00000017.JPEG
ILSVRC2012_test_00000018.JPEG
ILSVRC2012_test_00000019.JPEG
ILSVRC2012_test_00000020.JPEG
ILSVRC2012_test_00000021.JPEG
ILSVRC2012_test_00000022.JPEG
ILSVRC2012_test_00000023.JPEG
ILSVRC2012_test_00000024.JPEG
ILSVRC2012_test_00000025.JPEG
ILSVRC2012_test_00000026.JPEG
ILSVRC2012_test_00000027.JPEG
ILSVRC2012_test_00000028.JPEG
ILSVRC2012_test_00000029.JPEG
ILSVRC2012_test_00000030.JPEG
ILSVRC2012_test_00000031.JPEG
ILSVRC2012_test_00000032.JPEG
ILSVRC2012_test_00000033.JPEG
ILSVRC2012

ILSVRC2012_test_00000603.JPEG
ILSVRC2012_test_00000604.JPEG
ILSVRC2012_test_00000605.JPEG
ILSVRC2012_test_00000606.JPEG
ILSVRC2012_test_00000607.JPEG
ILSVRC2012_test_00000608.JPEG
ILSVRC2012_test_00000609.JPEG
ILSVRC2012_test_00000610.JPEG
ILSVRC2012_test_00000611.JPEG
ILSVRC2012_test_00000612.JPEG
ILSVRC2012_test_00000613.JPEG
ILSVRC2012_test_00000614.JPEG
ILSVRC2012_test_00000615.JPEG
ILSVRC2012_test_00000616.JPEG
ILSVRC2012_test_00000617.JPEG
ILSVRC2012_test_00000618.JPEG
ILSVRC2012_test_00000619.JPEG
ILSVRC2012_test_00000620.JPEG
ILSVRC2012_test_00000621.JPEG
ILSVRC2012_test_00000622.JPEG
ILSVRC2012_test_00000623.JPEG
ILSVRC2012_test_00000624.JPEG
ILSVRC2012_test_00000625.JPEG
ILSVRC2012_test_00000626.JPEG
ILSVRC2012_test_00000627.JPEG
ILSVRC2012_test_00000628.JPEG
ILSVRC2012_test_00000629.JPEG
ILSVRC2012_test_00000630.JPEG
ILSVRC2012_test_00000631.JPEG
ILSVRC2012_test_00000632.JPEG
ILSVRC2012_test_00000633.JPEG
ILSVRC2012_test_00000634.JPEG
ILSVRC2012_test_00000635.JPEG
ILSVRC2012

ILSVRC2012_test_00000997.JPEG
ILSVRC2012_test_00000998.JPEG
ILSVRC2012_test_00000999.JPEG
ILSVRC2012_test_00001000.JPEG
ILSVRC2012_test_00001001.JPEG
ILSVRC2012_test_00001002.JPEG
ILSVRC2012_test_00001003.JPEG
ILSVRC2012_test_00001004.JPEG
ILSVRC2012_test_00001005.JPEG
ILSVRC2012_test_00001006.JPEG
ILSVRC2012_test_00001007.JPEG
ILSVRC2012_test_00001008.JPEG
ILSVRC2012_test_00001009.JPEG
ILSVRC2012_test_00001010.JPEG
ILSVRC2012_test_00001011.JPEG
ILSVRC2012_test_00001012.JPEG
ILSVRC2012_test_00001013.JPEG
ILSVRC2012_test_00001014.JPEG
ILSVRC2012_test_00001015.JPEG
ILSVRC2012_test_00001016.JPEG
ILSVRC2012_test_00001017.JPEG
ILSVRC2012_test_00001018.JPEG
ILSVRC2012_test_00001019.JPEG
ILSVRC2012_test_00001020.JPEG
ILSVRC2012_test_00001021.JPEG
ILSVRC2012_test_00001022.JPEG
ILSVRC2012_test_00001023.JPEG
ILSVRC2012_test_00001024.JPEG
ILSVRC2012_test_00001025.JPEG
ILSVRC2012_test_00001026.JPEG
ILSVRC2012_test_00001027.JPEG
ILSVRC2012_test_00001028.JPEG
ILSVRC2012_test_00001029.JPEG
ILSVRC2012

ILSVRC2012_test_00001352.JPEG
ILSVRC2012_test_00001353.JPEG
ILSVRC2012_test_00001354.JPEG
ILSVRC2012_test_00001355.JPEG
ILSVRC2012_test_00001356.JPEG
ILSVRC2012_test_00001357.JPEG
ILSVRC2012_test_00001358.JPEG
ILSVRC2012_test_00001359.JPEG
ILSVRC2012_test_00001360.JPEG
ILSVRC2012_test_00001361.JPEG
ILSVRC2012_test_00001362.JPEG
ILSVRC2012_test_00001363.JPEG
ILSVRC2012_test_00001364.JPEG
ILSVRC2012_test_00001365.JPEG
ILSVRC2012_test_00001366.JPEG
ILSVRC2012_test_00001367.JPEG
ILSVRC2012_test_00001368.JPEG
ILSVRC2012_test_00001369.JPEG
ILSVRC2012_test_00001370.JPEG
ILSVRC2012_test_00001371.JPEG
ILSVRC2012_test_00001372.JPEG
ILSVRC2012_test_00001373.JPEG
ILSVRC2012_test_00001374.JPEG
ILSVRC2012_test_00001375.JPEG
ILSVRC2012_test_00001376.JPEG
ILSVRC2012_test_00001377.JPEG
ILSVRC2012_test_00001378.JPEG
ILSVRC2012_test_00001379.JPEG
ILSVRC2012_test_00001380.JPEG
ILSVRC2012_test_00001381.JPEG
ILSVRC2012_test_00001382.JPEG
ILSVRC2012_test_00001383.JPEG
ILSVRC2012_test_00001384.JPEG
ILSVRC2012

ILSVRC2012_test_00001717.JPEG
ILSVRC2012_test_00001718.JPEG
ILSVRC2012_test_00001719.JPEG
ILSVRC2012_test_00001720.JPEG
ILSVRC2012_test_00001721.JPEG
ILSVRC2012_test_00001722.JPEG
ILSVRC2012_test_00001723.JPEG
ILSVRC2012_test_00001724.JPEG
ILSVRC2012_test_00001725.JPEG
ILSVRC2012_test_00001726.JPEG
ILSVRC2012_test_00001727.JPEG
ILSVRC2012_test_00001728.JPEG
ILSVRC2012_test_00001729.JPEG
ILSVRC2012_test_00001730.JPEG
ILSVRC2012_test_00001731.JPEG
ILSVRC2012_test_00001732.JPEG
ILSVRC2012_test_00001733.JPEG
ILSVRC2012_test_00001734.JPEG
ILSVRC2012_test_00001735.JPEG
ILSVRC2012_test_00001736.JPEG
ILSVRC2012_test_00001737.JPEG
ILSVRC2012_test_00001738.JPEG
ILSVRC2012_test_00001739.JPEG
ILSVRC2012_test_00001740.JPEG
ILSVRC2012_test_00001741.JPEG
ILSVRC2012_test_00001742.JPEG
ILSVRC2012_test_00001743.JPEG
ILSVRC2012_test_00001744.JPEG
ILSVRC2012_test_00001745.JPEG
ILSVRC2012_test_00001746.JPEG
ILSVRC2012_test_00001747.JPEG
ILSVRC2012_test_00001748.JPEG
ILSVRC2012_test_00001749.JPEG
ILSVRC2012

...

ILSVRC2012_test_00098417.JPEG
ILSVRC2012_test_00098418.JPEG
ILSVRC2012_test_00098419.JPEG
ILSVRC2012_test_00098420.JPEG
ILSVRC2012_test_00098421.JPEG
ILSVRC2012_test_00098422.JPEG
ILSVRC2012_test_00098423.JPEG
ILSVRC2012_test_00098424.JPEG
ILSVRC2012_test_00098425.JPEG
ILSVRC2012_test_00098426.JPEG
ILSVRC2012_test_00098427.JPEG
ILSVRC2012_test_00098428.JPEG
ILSVRC2012_test_00098429.JPEG
ILSVRC2012_test_00098430.JPEG
ILSVRC2012_test_00098431.JPEG
ILSVRC2012_test_00098432.JPEG
ILSVRC2012_test_00098433.JPEG
ILSVRC2012_test_00098434.JPEG
ILSVRC2012_test_00098435.JPEG
ILSVRC2012_test_00098436.JPEG
ILSVRC2012_test_00098437.JPEG
ILSVRC2012_test_00098438.JPEG
ILSVRC2012_test_00098439.JPEG
ILSVRC2012_test_00098440.JPEG
ILSVRC2012_test_00098441.JPEG
ILSVRC2012_test_00098442.JPEG
ILSVRC2012_test_00098443.JPEG
ILSVRC2012_test_00098444.JPEG
ILSVRC2012_test_00098445.JPEG
ILSVRC2012_test_00098446.JPEG
ILSVRC2012_test_00098447.JPEG
ILSVRC2012_test_00098448.JPEG
ILSVRC2012_test_00098449.JPEG
ILSVRC2012

ILSVRC2012_test_00098759.JPEG
ILSVRC2012_test_00098760.JPEG
ILSVRC2012_test_00098761.JPEG
ILSVRC2012_test_00098762.JPEG
ILSVRC2012_test_00098763.JPEG
ILSVRC2012_test_00098764.JPEG
ILSVRC2012_test_00098765.JPEG
ILSVRC2012_test_00098766.JPEG
ILSVRC2012_test_00098767.JPEG
ILSVRC2012_test_00098768.JPEG
ILSVRC2012_test_00098769.JPEG
ILSVRC2012_test_00098770.JPEG
ILSVRC2012_test_00098771.JPEG
ILSVRC2012_test_00098772.JPEG
ILSVRC2012_test_00098773.JPEG
ILSVRC2012_test_00098774.JPEG
ILSVRC2012_test_00098775.JPEG
ILSVRC2012_test_00098776.JPEG
ILSVRC2012_test_00098777.JPEG
ILSVRC2012_test_00098778.JPEG
ILSVRC2012_test_00098779.JPEG
ILSVRC2012_test_00098780.JPEG
ILSVRC2012_test_00098781.JPEG
ILSVRC2012_test_00098782.JPEG
ILSVRC2012_test_00098783.JPEG
ILSVRC2012_test_00098784.JPEG
ILSVRC2012_test_00098785.JPEG
ILSVRC2012_test_00098786.JPEG
ILSVRC2012_test_00098787.JPEG
ILSVRC2012_test_00098788.JPEG
ILSVRC2012_test_00098789.JPEG
ILSVRC2012_test_00098790.JPEG
ILSVRC2012_test_00098791.JPEG
ILSVRC2012

ILSVRC2012_test_00099123.JPEG
ILSVRC2012_test_00099124.JPEG
ILSVRC2012_test_00099125.JPEG
ILSVRC2012_test_00099126.JPEG
ILSVRC2012_test_00099127.JPEG
ILSVRC2012_test_00099128.JPEG
ILSVRC2012_test_00099129.JPEG
ILSVRC2012_test_00099130.JPEG
ILSVRC2012_test_00099131.JPEG
ILSVRC2012_test_00099132.JPEG
ILSVRC2012_test_00099133.JPEG
ILSVRC2012_test_00099134.JPEG
ILSVRC2012_test_00099135.JPEG
ILSVRC2012_test_00099136.JPEG
ILSVRC2012_test_00099137.JPEG
ILSVRC2012_test_00099138.JPEG
ILSVRC2012_test_00099139.JPEG
ILSVRC2012_test_00099140.JPEG
ILSVRC2012_test_00099141.JPEG
ILSVRC2012_test_00099142.JPEG
ILSVRC2012_test_00099143.JPEG
ILSVRC2012_test_00099144.JPEG
ILSVRC2012_test_00099145.JPEG
ILSVRC2012_test_00099146.JPEG
ILSVRC2012_test_00099147.JPEG
ILSVRC2012_test_00099148.JPEG
ILSVRC2012_test_00099149.JPEG
ILSVRC2012_test_00099150.JPEG
ILSVRC2012_test_00099151.JPEG
ILSVRC2012_test_00099152.JPEG
ILSVRC2012_test_00099153.JPEG
ILSVRC2012_test_00099154.JPEG
ILSVRC2012_test_00099155.JPEG
ILSVRC2012

ILSVRC2012_test_00099487.JPEG
ILSVRC2012_test_00099488.JPEG
ILSVRC2012_test_00099489.JPEG
ILSVRC2012_test_00099490.JPEG
ILSVRC2012_test_00099491.JPEG
ILSVRC2012_test_00099492.JPEG
ILSVRC2012_test_00099493.JPEG
ILSVRC2012_test_00099494.JPEG
ILSVRC2012_test_00099495.JPEG
ILSVRC2012_test_00099496.JPEG
ILSVRC2012_test_00099497.JPEG
ILSVRC2012_test_00099498.JPEG
ILSVRC2012_test_00099499.JPEG
ILSVRC2012_test_00099500.JPEG
ILSVRC2012_test_00099501.JPEG
ILSVRC2012_test_00099502.JPEG
ILSVRC2012_test_00099503.JPEG
ILSVRC2012_test_00099504.JPEG
ILSVRC2012_test_00099505.JPEG
ILSVRC2012_test_00099506.JPEG
ILSVRC2012_test_00099507.JPEG
ILSVRC2012_test_00099508.JPEG
ILSVRC2012_test_00099509.JPEG
ILSVRC2012_test_00099510.JPEG
ILSVRC2012_test_00099511.JPEG
ILSVRC2012_test_00099512.JPEG
ILSVRC2012_test_00099513.JPEG
ILSVRC2012_test_00099514.JPEG
ILSVRC2012_test_00099515.JPEG
ILSVRC2012_test_00099516.JPEG
ILSVRC2012_test_00099517.JPEG
ILSVRC2012_test_00099518.JPEG
ILSVRC2012_test_00099519.JPEG
ILSVRC2012

ILSVRC2012_test_00099849.JPEG
ILSVRC2012_test_00099850.JPEG
ILSVRC2012_test_00099851.JPEG
ILSVRC2012_test_00099852.JPEG
ILSVRC2012_test_00099853.JPEG
ILSVRC2012_test_00099854.JPEG
ILSVRC2012_test_00099855.JPEG
ILSVRC2012_test_00099856.JPEG
ILSVRC2012_test_00099857.JPEG
ILSVRC2012_test_00099858.JPEG
ILSVRC2012_test_00099859.JPEG
ILSVRC2012_test_00099860.JPEG
ILSVRC2012_test_00099861.JPEG
ILSVRC2012_test_00099862.JPEG
ILSVRC2012_test_00099863.JPEG
ILSVRC2012_test_00099864.JPEG
ILSVRC2012_test_00099865.JPEG
ILSVRC2012_test_00099866.JPEG
ILSVRC2012_test_00099867.JPEG
ILSVRC2012_test_00099868.JPEG
ILSVRC2012_test_00099869.JPEG
ILSVRC2012_test_00099870.JPEG
ILSVRC2012_test_00099871.JPEG
ILSVRC2012_test_00099872.JPEG
ILSVRC2012_test_00099873.JPEG
ILSVRC2012_test_00099874.JPEG
ILSVRC2012_test_00099875.JPEG
ILSVRC2012_test_00099876.JPEG
ILSVRC2012_test_00099877.JPEG
ILSVRC2012_test_00099878.JPEG
ILSVRC2012_test_00099879.JPEG
ILSVRC2012_test_00099880.JPEG
ILSVRC2012_test_00099881.JPEG
ILSVRC2012

In [61]:
file_tst_tar.unlink()

In [62]:
shutil.copy('test.txt', dir_tst/'tst.txt')

PosixPath('/data/IMAGENET/2012/TST/tst.txt')

### Match codes to synsets and words

In [64]:
shutil.copy('synset_words.txt', dir_imagenet_2012)

'/data/IMAGENET/2012/synset_words.txt'

Read synset to words table

In [65]:
file_synset_words = dir_imagenet_2012/'synset_words.txt'

In [72]:
df_synset_words = pd.read_table(file_synset_words, header=None)

In [81]:
df_synset_words[['synset','words']] = df_synset_words[0].str.split(' ', 1, expand=True)
df_synset_words.drop(columns=[0], inplace=True)
df_synset_words.head()

synset                                              words
0  n01440764                                 tench, Tinca tinca
1  n01443537                        goldfish, Carassius auratus
2  n01484850  great white shark, white shark, man-eater, man...
3  n01491361                    tiger shark, Galeocerdo cuvieri
4  n01494475                       hammerhead, hammerhead shark

Get codes dataframes; start by reading the train text file

In [97]:
df_synset_codes = pd.read_table(dir_imagenet_2012/'TRN'/'trn.txt', header=None)

In [98]:
df_synset_codes[['path','code']] = df_synset_codes[0].str.split(' ', 1, expand=True)
df_synset_codes.drop(columns=[0], inplace=True)
df_synset_codes.head()

path code
0  n01440764/n01440764_10026.JPEG    0
1  n01440764/n01440764_10027.JPEG    0
2  n01440764/n01440764_10029.JPEG    0
3  n01440764/n01440764_10040.JPEG    0
4  n01440764/n01440764_10042.JPEG    0

In [99]:
df_synset_codes['synset'] = df_synset_codes['path'].str.split('/', 0, expand=True)[0]
df_synset_codes.drop(columns=['path'], inplace=True)
df_synset_codes.head()

code     synset
0    0  n01440764
1    0  n01440764
2    0  n01440764
3    0  n01440764
4    0  n01440764

In [101]:
df_synset_codes = df_synset_codes.drop_duplicates()
df_synset_codes.head()

code     synset
0       0  n01440764
1300    1  n01443537
2600    2  n01484850
3900    3  n01491361
5200    4  n01494475

In [107]:
df_synset_words_and_codes = df_synset_words.merge(df_synset_codes, on='synset')
df_synset_words_and_codes

synset                                              words code
0    n01440764                                 tench, Tinca tinca    0
1    n01443537                        goldfish, Carassius auratus    1
2    n01484850  great white shark, white shark, man-eater, man...    2
3    n01491361                    tiger shark, Galeocerdo cuvieri    3
4    n01494475                       hammerhead, hammerhead shark    4
..         ...                                                ...  ...
995  n13044778                                          earthstar  995
996  n13052670  hen-of-the-woods, hen of the woods, Polyporus ...  996
997  n13054560                                             bolete  997
998  n13133613                              ear, spike, capitulum  998
999  n15075141       toilet tissue, toilet paper, bathroom tissue  999

[1000 rows x 3 columns]

In [108]:
df_synset_words_and_codes.to_csv(dir_imagenet_2012/'synset_words_and_codes.csv', index=False)

In [109]:
shutil.copy(dir_imagenet_2012/'synset_words_and_codes.csv', 'synset_words_and_codes.csv')

'synset_words_and_codes.csv'